In [1]:
"""
Author(s): Steven van den Broek, Yuqin Cui
Created: 2019-05-08
Edited: 2019-05-13
"""

'\nAuthor(s): Steven van den Broek, Yuqin Cui\nCreated: 2019-05-08\nEdited: 2019-05-13\n'

In [2]:
import numpy as np
import pandas as pd
import panel as pn
import param
import hvplot.pandas
import holoviews as hv
from holoviews import opts, streams
from bokeh.models import CustomJS, BoxSelectTool, ColumnDataSource
from colorcet import palette
from bokeh.models.widgets.buttons import Button


from holoviews.streams import Selection1D


In [3]:
# import numpy as np
# import holoviews as hv
# from holoviews import opts
# from holoviews.streams import Selection1D
# from bokeh.models import BoxSelectTool
# import panel as pn
# import param
# import pandas as pd
# from colorcet import palette
# from bokeh.models.widgets.buttons import Button

In [4]:
fname = 'GephiMatrix_author_similarity.csv'
f = open(fname, 'r')

# Get author names
line1 = f.readline()
names = line1[1:].split(';');

seen = {}
dupes = []

for index, name in enumerate(names):
    if name not in seen:
        seen[name] = 1
    else:
        if seen[name] == 1:
            dupes.append((index, name))
        seen[name] += 1

# add 1, 2 etc after the name
for pair in dupes:
    index = pair[0]
    name = pair[1]
    for i in range(seen[name]):
        names[index] = name + str((i+1))
        #print(names[index])

# Read csv
df = pd.read_csv(f, names=names, sep=';')

# Fix it
df = df.reset_index(level=1)
names.append("delete")
names = [name.replace('_', ' ') for name in names]
df.columns = names
del df["delete"]
df.set_index([df.columns], inplace=True)

# Get names again for later use
names = df.columns.tolist()

# Get 150*150 sub matrix since otherwise the plot is very slow..
df = df.head(150)[names[0:150]]
names = df.columns.tolist()

df_original = df.copy()

In [5]:
#convert similarity into unsimilarity (1.0 - similarity)
for name in names:
    df[name] = 1 - df[name]

In [6]:
import numpy as np
from scipy.spatial.distance import pdist, squareform
from sklearn import datasets
from fastcluster import linkage

In [7]:
# The output of linkage is stepwise dendrogram, 
# which is represented as an (N − 1) × 4 NumPy array with floating point entries (dtype=numpy.double). 
# The first two columns contain the node indices which are joined in each step. The input nodes are
# labeled 0,..., N − 1, and the newly generated nodes have the labels N,...2N-2.
# The third column contains the distance between the two nodes at each step, ie. the
# current minimal distance at the time of the merge. The fourth column counts the
# number of points which comprise each new node.

#Idea is from: https://gmarti.gitlab.io/ml/2017/09/07/how-to-sort-distance-matrix.html

#Traversal the hierarhical tree generated by linkage
def traversal_tree(hier_tree,number_of_node, current_index):
    if current_index < number_of_node:
        return [current_index]
    else:
        return (traversal_tree(hier_tree,number_of_node, int(hier_tree[current_index-number_of_node][1])) + 
                traversal_tree(hier_tree,number_of_node,int(hier_tree[current_index-number_of_node][0])))

In [8]:
def compute_serial_matrix(df,method="ward", dist_metric = "euclidean"):
    #define the dist_mat by different dist_metric mathod in fast_clustering package
    dist_mat = squareform(pdist(df, metric=dist_metric))    
    #hierar tree was got from package "fast-clustering"
    hierar_tree = linkage(squareform(dist_mat), method=method,preserve_input=True)   
    #The order implied by the hierarhical tree
    reordered_index = traversal_tree(hierar_tree, len(dist_mat), 2*len(dist_mat)-2)
    return reordered_index, hierar_tree


#linkage(squareform(pdist(df, metric="euclidean")), method="ward",preserve_input=True)

In [9]:
#order original matrix based on index provided
def author_reorder_list(df,order):
    new_names = df.columns
    return [new_names[i] for i in order]

def reordercol(df, order):
    secondIndex = []
    new_df = df
    new_df['nindex'] = np.arange(len(new_df))
    for i in order:
        secondIndex += new_df.index[new_df['nindex'] == i].tolist()
    new_df.drop('nindex',axis=1, inplace = True)
    a = new_df.reindex( index = secondIndex)
    return a

def reorderrow(df, order):
    a = df.values
    permutation = order
    return a[:,permutation]

def reorder_input_df(df, order):
    reorder_col = reordercol(df, order)
    finish = reorderrow(reorder_col, order)
    return finish

In [10]:
def to_liquid(matrix):
    solid = pd.DataFrame(matrix)
    solid.index = names
    solid.columns = names
    solid.reset_index(inplace=True)
    liquid = solid.melt(id_vars='index', value_vars=list(df.columns[0:]), var_name="name2")
    liquid.columns = ['index2', 'index1', 'value']
    liquid = liquid[['index1', 'index2', 'value']]
    #print(liquid)
    return liquid



In [11]:
def to_liquid_2(matrix, df, order):
    solid = pd.DataFrame(matrix)
    name_list = author_reorder_list(df, order)
    #print(name_list)
    solid.index = name_list
    solid.columns = name_list
    solid.reset_index(inplace=True)
    liquid = solid.melt(id_vars='index', value_vars=list(name_list[0:]), var_name="name2")
    liquid.columns = ['index2', 'index1', 'value']
    liquid = liquid[['index1', 'index2', 'value']]
    #print(liquid)
    return liquid

In [12]:
#to_liquid(df.values)

In [13]:
# res_order, res_linkage = compute_serial_matrix(df_original,"ward")
# reordered_matrix = reorder_input_df(df_original, res_order)
# #print(to_liquid(df.values))

# author_reorder_list(df, res_order)
# to_liquid_2(reordered_matrix,df, res_order)

In [14]:
def dis_to_similarity(grid):
    nrows = len(grid)
    ncols = len(grid[0])
    for i in range(nrows):
        for j in range(ncols):
            grid[i][j] = 1 - grid[i][j]            

In [15]:
#callback = CustomJS(args=dict(), code="""
#console.log(cb_obj)
#console.log(cb_data)
#""")

# def print_info(*args, **kwargs):
#     indices = kwargs['index']
#     for i in indices:
#         j = len(names)-1-(i%len(names))+i//(len(names))*(len(names))
#         print("old: {}, new: {}".format(i, j))
#         for value in current_data.loc[j]:
#             print(value)
        
#     print()
        
# def say_hello(*args, **kwargs):
#     print("Hi")

In [16]:
pn.extension()
select_tool = BoxSelectTool()

result = to_liquid(df_original.values)
hm = hv.HeatMap(result).opts(tools=['tap', select_tool, 'hover'],active_tools=['box_select'],
          height=550, width=600, xaxis=None, yaxis=None, cmap=palette['kbc'])
current_data = hm.data

class Matrix_dropdown(param.Parameterized):
    reordering = param.ObjectSelector(default="none",objects=["none","single","average","complete", "centroid", "weighted", "median","ward"])
    metric = param.ObjectSelector(default="euclidean", objects=["euclidean", "minkowski", "cityblock", "sqeuclidean", "cosine", "correlation", "hamming", "jaccard", "chebyshev", "canberra", "braycurtis"])
    def view(self):
        global selection
        global current_data
        global hm
        if self.reordering == "none":
            # if 'selection' in globals():
            #     selection.clear()
                
            result = to_liquid(df_original.values)
            #return result.hvplot.heatmap('index1', 'index2', 'value', invert=True, tools=['tap', select_tool],
            #          height=500, width=600, flip_yaxis=True, xaxis=None, yaxis=None, cmap=palette['kbc'])
            
            hm = hv.HeatMap(result).opts(tools=['tap', select_tool, 'hover'],active_tools=['box_select'],
                      height=550, width=600, xaxis=None, yaxis=None, cmap=palette['kbc'])
            current_data = hm.data
            return hm
            # selection = Selection1D(source=hm, subscribers=[print_info])
            # return hv.DynamicMap(lambda index: hm, streams=[selection])
        else:
            if 'selection' in globals():
                selection.clear()
            res_order, res_linkage = compute_serial_matrix(df,self.reordering, dist_metric = self.metric)
            reordered_matrix_col = reordercol(df, res_order)
            reordered_matrix = reorderrow(reordered_matrix_col, res_order)
            dis_to_similarity(reordered_matrix) 
            #reordered_matrix = pd.DataFrame(reordered_matrix, index = author_reorder_list(df,res_order), column = author_reorder_list(df,res_order))
            result = to_liquid_2(reordered_matrix, df, res_order)
            hm = hv.HeatMap(result).opts(tools=['tap', select_tool, 'hover'],active_tools=['box_select'],
                      height=550, width=600, xaxis=None, yaxis=None, cmap=palette['kbc'])
            current_data = hm.data
            return hm
            # selection = Selection1D(source=hm, subscribers=[print_info])
            # return hv.DynamicMap(lambda index: hm, streams=[selection])


# def update_selection_programmatically():
#     selection.event(index = [12000])

# bt = Button(
#     label="Update Selection",
#     button_type="success",
#     width=50
# )

# bt.on_click(update_selection_programmatically)

matrix = Matrix_dropdown(name='Adjacency Matrix')


In [58]:
from holoviews.plotting.bokeh.callbacks import LinkCallback
from holoviews.plotting.links import Link

class SelectLink(Link):
    _requires_target = True

class SelectCallback(LinkCallback):
    
    source_model = 'selected'
    source_handles = ['cds']
    on_source_changes = ['indices']

    target_model = 'selected'
    
    source_code = "let len = {}" .format(len(names)) + """
        let new_indices = []
        for (let i = 0; i < source_selected.indices.length; i++){
            let index = source_selected.indices[i]
            console.log(index)
            j = len-1-(index%len)+Math.floor(index/(len))*(len)
            console.log(j)
            new_indices[i] = j
        }
        target_selected.indices = new_indices
    """

SelectLink.register_callback('bokeh', SelectCallback)

table = hv.Table(current_data)
SelectLink(hm, table)
SelectLink(table, hm)
# hv_plot = hm + table
matrix_pane = pn.Row(hm, table)

In [59]:
len(names)

150

In [60]:
matrix_pane.servable()

Row
    [0] HoloViews(HeatMap)
    [1] HoloViews(Table)

In [19]:
#test_hm = hv.HeatMap(to_liquid(df_original)).opts(opts.HeatMap(tools=['tap', select_tool, 'hover'],active_tools=['box_select'],
#                      height=550, width=600, xaxis=None, yaxis=None, cmap=palette['kbc']))

In [20]:
#fig = hv.render(test_hm)
#fig.name = "heatmap"

In [21]:
#fig.name

In [22]:
#fig.select(name="heatmap")

In [23]:
renderer = hv.renderer('bokeh')
plot = renderer.get_plot(hm)

In [24]:
plot.handles.keys()

dict_keys(['hover', 'xaxis', 'x_range', 'yaxis', 'y_range', 'plot', 'color_mapper', 'color_dim', 'previous_id', 'source', 'cds', 'selected', 'glyph', 'glyph_renderer'])

In [25]:
plot.handles['glyph']

Rect(id='1180', ...)

In [26]:
plot.handles['cds'].selected.indices

[]

In [27]:
#test_hm

In [28]:
from bokeh.io import output_file, show
from bokeh.layouts import gridplot
from bokeh.models import ColumnDataSource
from bokeh.plotting import figure

x = list(range(-20, 21))
y0 = [abs(xx) for xx in x]
y1 = [xx**2 for xx in x]

# create a column data source for the plots to share
source = ColumnDataSource(data=dict(x=x, y0=y0, y1=y1))

TOOLS = "box_select,lasso_select,help"

# create a new plot and add a renderer
left = figure(tools=TOOLS, plot_width=300, plot_height=300, title=None)
left.circle('x', 'y0', source=source)
# show(left)

GlyphRenderer(id='1224', ...)

In [29]:
source.selected.update(indices=[4])

In [30]:
from bokeh.io import curdoc
from bokeh.models import ColumnDataSource
from bokeh.plotting import figure
from bokeh.layouts import column
from bokeh.models.tools import LassoSelectTool, TapTool

from bokeh.models.callbacks import CustomJS

source = ColumnDataSource(dict(
    x=[1, 2, 3, 4, 5, 6],
    y=[1, 2, 3, 4, 5, 6],
))

p = figure(
    plot_height=300,
    tools='',
)
p.circle( x='x', y='y', size=20, source=source)

lasso_select = LassoSelectTool(
    select_every_mousemove=False,
)
tap = TapTool()
tools = (lasso_select, tap)
p.add_tools(*tools)

def update_selection_programmatically():
    source.selected.update(indices=[4])
bt = Button(
    label="Update Selection",
    button_type="success",
    width=50
)

bt.on_click(update_selection_programmatically)


def update_selection(attr, old, new):
    print('>> NEW SELECTION: {}'.format(new.indices))
    # new.indices = [0]       # this works fine here

source.on_change('selected', update_selection)

#pn.Column(p, bt).servable()

In [31]:
source.selected.indices

[]

In [32]:
source.selected.update(indices=[4])

In [33]:
source.selected.indices

[4]

In [34]:

# hv.extension('bokeh')
# lin = np.linspace(-np.pi,np.pi,300)

# def lissajous(t, a=3, b=5, delta=np.pi/2.):
#     return (np.sin(a * t + delta), np.sin(b * t))

# def lissajous_crosshair(t, a=3, b=5, delta=np.pi/2):
#     (x,y) = lissajous(t,a,b,delta)
#     return hv.VLine(x) * hv.HLine(y)

# crosshair = hv.DynamicMap(lissajous_crosshair, kdims='t').redim.range(t=(-3.,3.))

# path = hv.Path(lissajous(lin))

# path * crosshair